# ASR Streaming Benchmark
---
Benchmark streaming ASR backends (Whisper, Parakeet, Vosk, FastConformer) with configurable parameters.

**Metrics:** WER (Word Error Rate), Latency (ms), RTF (Real-Time Factor)  
**Workflow:** Setup → Configure → Generate Audio → Benchmark → Analyze → Export

**Features:**
- Interactive backend configuration with custom variants
- Real-time audio generation with Ollama + gTTS
- Comprehensive latency analysis (avg, P95, max)
- WER calculation for accuracy comparison
- Automatic export of raw results and summary JSON


# 1. Bootstrap & Setup

Install packages and import libraries.

In [6]:
# Install required packages (China mirrors for faster downloads)
%pip install -q jiwer nest_asyncio soundfile librosa matplotlib seaborn pandas websockets panel -i https://pypi.tuna.tsinghua.edu.cn/simple

Note: you may need to restart the kernel to use updated packages.


In [7]:
import warnings
import matplotlib.pyplot as plt
import nest_asyncio
import seaborn as sns

warnings.filterwarnings('ignore')

# Enable nested event loops for Jupyter
nest_asyncio.apply()

# Set plot style
sns.set_style('whitegrid')
plt.rcParams['figure.figsize'] = (12, 6)

# 2. Generate Test Audio

Generate test audio with Ollama + gTTS or upload your own audio file for benchmarking.

In [ ]:
# Audio Generation Settings
word_count = 500      # Number of words to generate
speech_speed = 1.5    # Speech speed multiplier (1.0 = normal, 1.5 = faster)

print(f"⚙️ Audio Generation Settings:")
print(f"   • Word Count: {word_count}")
print(f"   • Speech Speed: {speech_speed}x")

In [ ]:
import sys
from pathlib import Path
from IPython.display import display, Audio
import requests

# Add helpers directory to path
helpers_dir = Path().absolute() / "helpers"
if str(helpers_dir) not in sys.path:
    sys.path.insert(0, str(helpers_dir))

from audio_generation import generate_text_with_ollama, text_to_speech_gtts

# Initialize test config defaults (audio settings only)
test_config = {
    "chunk_duration": 1.0, 
    "sample_rate": 16000
}

# Unload GPU models before text generation to free memory for Ollama
print("🔄 Unloading GPU models to free memory for Ollama...")
BACKEND_URLS = {
    'vosk': 'http://vosk-asr:8000',
    'parakeet': 'http://parakeet-asr:8000',
    'whisper': 'http://whisper-asr:8000',
    'fastconformer': 'http://fastconformer-asr:8000'
}

for backend_name, backend_url in BACKEND_URLS.items():
    try:
        response = requests.post(f"{backend_url}/unload", timeout=5)
        if response.status_code == 200:
            print(f"  ✓ {backend_name}: GPU models unloaded")
        else:
            print(f"  ⚠ {backend_name}: unload returned status {response.status_code}")
    except Exception as e:
        print(f"  ⚠ {backend_name}: {e}")

print()

# Generate audio
print("🎙️ Generating test audio...")
sample_rate = test_config.get('sample_rate', 16000)

print(f"⚙️ Settings: {word_count} words, {speech_speed}x speed, {sample_rate}Hz")

# Generate text
text = generate_text_with_ollama(word_count=word_count)

# Convert to speech
audio_data = text_to_speech_gtts(text, sample_rate=sample_rate, speed=speech_speed)

print(f"✅ Audio generated! Duration: {len(audio_data)/sample_rate:.2f}s")

# Store for benchmarks
test_audio = (audio_data, text)

def get_test_audio():
    """Get the current audio data and transcript."""
    return test_audio

# Audio player
print(f"🔊 Audio Playback")
display(Audio(data=audio_data, rate=sample_rate, autoplay=False))

# Transcript preview
print(f"📄 Reference Transcript")
print(f"\n{text}")
print(f"\n📌 Use get_test_audio() to access audio and transcript for benchmarks")

🔄 Unloading GPU models to free memory for Ollama...
  ⚠ vosk: unload returned status 404
  ✓ parakeet: GPU models unloaded
  ✓ whisper: GPU models unloaded
  ✓ fastconformer: GPU models unloaded

🎙️ Generating test audio...
⚙️ Settings: 500 words, 1.5x speed, 16000Hz
✓ Generated text from Ollama model 'qwen3:14b' (471 words)
✓ Generated audio: 2491904 samples (155.74s) at 1.5x speed
✅ Audio generated! Duration: 155.74s
🔊 Audio Playback


📄 Reference Transcript

Imagine this: You’re scrolling through your phone, and before you’ve even finished typing, your device suggests the perfect song, movie, or even a solution to a problem you didn’t know you had. This isn’t magic—it’s artificial intelligence (AI), working quietly behind the scenes to shape your day. From the moment you wake up to the moment you go to bed, AI is probably influencing your life in ways you’ve never stopped to think about. And yet, for all its ubiquity, it’s still a force that sparks equal parts wonder and unease.  

AI’s rise isn’t just about convenience; it’s about transforming entire industries. In healthcare, algorithms now analyze medical images with precision that rivals—or even surpasses—human experts, spotting tumors in scans or predicting heart attacks before symptoms arise. In climate science, AI models simulate weather patterns and track deforestation, giving researchers tools to combat global warming. Even in education, adaptive learning p

## Option 2: Generate Audio with Ollama + gTTS

In [ ]:
import sys
from pathlib import Path
from IPython.display import display, Audio
import panel as pn

# Add helpers directory to path
helpers_dir = Path().absolute() / "helpers"
if str(helpers_dir) not in sys.path:
    sys.path.insert(0, str(helpers_dir))

from audio_generation import generate_text_with_ollama, text_to_speech_gtts

# Initialize Panel extension
pn.extension()

# Audio upload widget
file_input = pn.widgets.FileInput(accept='.wav,.mp3,.m4a,.ogg', name='Upload Audio File')
upload_button = pn.widgets.Button(name='Use Uploaded Audio', button_type='primary')
upload_status = pn.pane.Markdown('📤 Upload an audio file or generate new audio below')

# State variables
test_audio = (None, None)  # (audio_data, transcript)
sample_rate = 16000

def get_test_audio():
    """Get the current audio data and transcript."""
    return test_audio

async def process_uploaded_audio(event):
    """Process uploaded audio file and get reference transcript via offline ASR."""
    global test_audio, sample_rate
    
    if file_input.value is None:
        upload_status.object = '⚠️ No file uploaded'
        return
    
    upload_status.object = '🔄 Processing uploaded audio...'
    
    try:
        import soundfile as sf
        import io
        import numpy as np
        
        # Read uploaded audio
        audio_bytes = file_input.value
        audio_file = io.BytesIO(audio_bytes)
        audio_data, file_sr = sf.read(audio_file)
        
        # Convert to mono if stereo
        if len(audio_data.shape) > 1:
            audio_data = audio_data.mean(axis=1)
        
        # Resample to 16kHz if needed
        if file_sr != sample_rate:
            import librosa
            audio_data = librosa.resample(audio_data, orig_sr=file_sr, target_sr=sample_rate)
        
        # Normalize to float32 [-1, 1]
        if audio_data.dtype != np.float32:
            audio_data = audio_data.astype(np.float32)
        if np.abs(audio_data).max() > 1.0:
            audio_data = audio_data / np.abs(audio_data).max()
        
        upload_status.object = f'✅ Audio loaded ({len(audio_data)/sample_rate:.2f}s)<br/>🔄 Getting reference transcript via Whisper offline...'
        
        # Use Whisper offline transcription for most accurate reference
        import requests
        audio_int16 = (audio_data * 32767).astype(np.int16)
        
        response = requests.post(
            'http://whisper-asr:8000/transcribe',
            files={'file': ('audio.wav', audio_int16.tobytes(), 'audio/wav')},
            data={'sample_rate': sample_rate},
            timeout=120
        )
        
        if response.status_code == 200:
            result = response.json()
            transcript = result.get('text', '')
            
            test_audio = (audio_data, transcript)
            
            upload_status.object = f'''✅ Audio uploaded and transcribed!
**Duration:** {len(audio_data)/sample_rate:.2f}s  
**Reference Transcript:** {transcript[:200]}{'...' if len(transcript) > 200 else ''}'''
            
            # Display audio player
            display(Audio(data=audio_data, rate=sample_rate, autoplay=False))
        else:
            upload_status.object = f'❌ Transcription failed: {response.status_code}'
    
    except Exception as e:
        upload_status.object = f'❌ Error: {str(e)}'

upload_button.on_click(process_uploaded_audio)

# Display upload interface
upload_ui = pn.Column(
    pn.pane.Markdown('## Option 1: Upload Audio'),
    file_input,
    upload_button,
    upload_status,
    width=600
)

display(upload_ui)

# 3. Model Configuration

Configure ASR backends, parameters, and test settings. Add model variants with different configurations.

**Note:** Audio settings (Chunk Duration, Sample Rate) are used for streaming transcription.

In [8]:
import sys
from pathlib import Path

# Force complete module reload
for module in list(sys.modules.keys()):
    if 'config_ui' in module:
        del sys.modules[module]

# Add helpers directory to path
helpers_dir = Path().absolute() / "helpers"
if str(helpers_dir) not in sys.path:
    sys.path.insert(0, str(helpers_dir))

from config_ui import create_configuration_ui

# ASR Service Endpoints (already defined earlier, but repeated for clarity)
BACKEND_URLS = {
    'vosk': 'http://vosk-asr:8000',
    'parakeet': 'http://parakeet-asr:8000',
    'whisper': 'http://whisper-asr:8000',
    'fastconformer': 'http://fastconformer-asr:8000'
}

# Backend-specific configuration options
BACKEND_OPTIONS = {
    'whisper': {
        'VAD_FILTER': True, 
        'VAD_THRESHOLD': 0.5, 
        'BEAM_SIZE': 5, 
        'LANGUAGE': 'en',
        'CHUNK_DURATION_SEC': 1.5,
        'MIN_AUDIO_SEC': 0.3
    },
    'parakeet': {'DECODING_STRATEGY': 'greedy', 'BEAM_SIZE': 1, 'LANGUAGE': 'en'},
    'fastconformer': {'ATT_CONTEXT_SIZE': 8, 'DECODER_TYPE': 'rnnt', 'BEAM_SIZE': 1, 'BATCH_SIZE': 1}
}

# State variables - use existing test_config from audio generation
variants = []

# Create UI
ui, helpers = create_configuration_ui(variants, test_config, BACKEND_URLS, BACKEND_OPTIONS)

# Extract helper functions
get_backends = helpers['get_backends']
get_config_raw = helpers['get_config']
show_variants = helpers['show_variants']
clear_all = helpers['clear_all']


def get_config():
    """Get configuration with calculated chunk_size."""
    config = get_config_raw()
    config['chunk_size'] = int(config['chunk_duration'] * config['sample_rate'])
    return config


print("✅ Configuration UI Ready!")
print("💡 Functions: get_backends(), get_config(), show_variants(), clear_all()")
print("📌 Audio settings (chunk duration, sample rate) are used for streaming transcription")
print()

# Display the UI
display(ui)

✅ Configuration UI Ready!
💡 Functions: get_backends(), get_config(), show_variants(), clear_all()
📌 Audio settings (chunk duration, sample rate) are used for streaming transcription



# 4. Run Benchmarks

Execute streaming benchmarks for all configured variants and save raw results for later analysis.

The raw results (`.pkl`) include all Python objects and can be reloaded to re-run analysis without re-benchmarking.

In [ ]:
from benchmark import run_all_benchmarks

print("✅ Benchmark functions loaded")
print("Starting benchmarks...")

benchmark_results = await run_all_benchmarks(
    get_backends(),
    get_test_audio()[0],  # audio data
    get_config()
)

# Store reference transcript
REFERENCE_TRANSCRIPT = get_test_audio()[1]  # transcript

print(f"\n✅ Benchmarks complete!")
print(f"📊 {len(benchmark_results)} results collected")

In [ ]:
import pickle
from datetime import datetime
from pathlib import Path

# Export raw benchmark results for reproducibility
timestamp = datetime.now().strftime("%Y%m%d%H%M")
output_dir = Path(".results")
output_dir.mkdir(parents=True, exist_ok=True)

# Save raw results with pickle (includes all Python objects)
raw_results_file = output_dir / f"benchmark_raw_{timestamp}.pkl"
with open(raw_results_file, 'wb') as f:
    pickle.dump({
        'results': benchmark_results,
        'reference_transcript': REFERENCE_TRANSCRIPT,
        'config': get_config(),
        'backends': get_backends(),
        'timestamp': timestamp
    }, f)

print(f"📦 Raw results saved to: {raw_results_file}")

# 5. Results Analysis

Analyze metrics, visualize latency, calculate WER, and export summary reports.

**Available Analyses:**
- Summary statistics table (avg/P95/max latency)
- WER calculation vs reference transcript  
- Latency distribution charts
- Latency over time progression
- JSON summary export


In [ ]:
# Load previously saved results for analysis
import pickle
from pathlib import Path

# Find the most recent raw results file
results_dir = Path(".results")
raw_files = sorted(results_dir.glob("benchmark_raw_*.pkl"), reverse=True)

if raw_files:
    with open(raw_files[0], 'rb') as f:
        saved_data = pickle.load(f)
    
    benchmark_results = saved_data['results']
    REFERENCE_TRANSCRIPT = saved_data['reference_transcript']
    
    print(f"✅ Loaded results from: {raw_files[0]}")
    print(f"📊 {len(benchmark_results)} benchmark results loaded")
else:
    print("⚠️ No saved results found in .results/ directory")
    print("💡 Run the benchmark cells first to generate results")

In [ ]:
from results_analysis import create_results_dataframe, print_results_summary

# Create and display results DataFrame
df_results = create_results_dataframe(benchmark_results)
print_results_summary(df_results)


In [ ]:
from results_analysis import calculate_wer_metrics

successful_results = [r for r in benchmark_results if r.get('success', False)]

# Calculate WER for each backend
calculate_wer_metrics(successful_results, REFERENCE_TRANSCRIPT)


In [ ]:
from results_analysis import create_results_dataframe

# Display results table (using df_results created earlier)
if 'df_results' not in locals():
    # Fallback: create from raw results
    df_results = create_results_dataframe(benchmark_results)

df_display = df_results.copy()

# Round for display
for col in ['wer', 'latency_ms', 'rtf']:
    if col in df_display.columns:
        df_display[col] = df_display[col].round(3)

print("=" * 80)
print("BENCHMARK RESULTS")
print("=" * 80)
display(df_display)

# Highlight best performers
if 'wer' in df_display.columns and not df_display['wer'].isna().all():
    best_wer_idx = df_display['wer'].idxmin()
    best_wer = df_display.loc[best_wer_idx]
    print(f"\n🏆 Best WER: {best_wer['backend']} ({best_wer.get('config', 'N/A')}) - {best_wer['wer']:.3f}")

if 'latency_ms' in df_display.columns and not df_display['latency_ms'].isna().all():
    best_latency_idx = df_display['latency_ms'].idxmin()
    best_latency = df_display.loc[best_latency_idx]
    print(f"⚡ Fastest Latency: {best_latency['backend']} ({best_latency.get('config', 'N/A')}) - {best_latency['latency_ms']:.1f}ms")

if 'rtf' in df_display.columns and not df_display['rtf'].isna().all():
    best_rtf_idx = df_display['rtf'].idxmin()
    best_rtf = df_display.loc[best_rtf_idx]
    print(f"🚀 Best RTF: {best_rtf['backend']} ({best_rtf.get('config', 'N/A')}) - {best_rtf['rtf']:.3f}")

## Visualization

In [ ]:
from results_analysis import plot_latency_comparison

# Plot latency comparison
successful_results = [r for r in benchmark_results if r.get('success', False)]
plot_latency_comparison(successful_results)


In [ ]:
from results_analysis import plot_latency_over_time

# Plot latency over time
plot_latency_over_time(successful_results)


## Export Results

In [ ]:
from datetime import datetime
from pathlib import Path

from results_analysis import export_results_json

# Export summary JSON (this was saved during benchmarks, create new one if needed)
timestamp = datetime.now().strftime("%Y%m%d%H%M")
output_dir = Path(".results")
output_dir.mkdir(parents=True, exist_ok=True)

# Export results summary to JSON
output_file = export_results_json(
    benchmark_results,
    test_audio,
    get_config(),
    output_file=str(output_dir / f"benchmark_summary_{timestamp}.json")
)

print(f"✅ Summary exported to: {output_file}")
print("💡 Raw results were saved during benchmark execution")